## ML Pipeline with Sklearn

In [1]:
# load sample dataset
import pandas as pd
import seaborn as sns

from ydata_profiling import ProfileReport

from sklearn.model_selection import train_test_split
from sklearn.datasets import make_regression
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.metrics import r2_score
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_absolute_percentage_error

from yellowbrick.regressor import PredictionError

df = pd.read_csv('./diabetes.csv')
print(df.shape)
df

(768, 9)


Number of times pregnant  \
0                           6   
1                           1   
2                           8   
3                           1   
4                           0   
..                        ...   
763                        10   
764                         2   
765                         5   
766                         1   
767                         1   

     Plasma glucose concentration a 2 hours in an oral glucose tolerance test  \
0                                                  148                          
1                                                   85                          
2                                                  183                          
3                                                   89                          
4                                                  137                          
..                                                 ...                          
763                                                101                          
764                                                122                          
765                                                121                          
766                                                126                          
767                                                 93                          

     Diastolic blood pressure (mm Hg)  Triceps skin fold thickness (mm)  \
0                                  72                                35   
1                                  66                                29   
2                                  64                                 0   
3                                  66                                23   
4                                  40                                35   
..                                ...                               ...   
763                                76                                48   
764                                70                                27   
765                                72                                23   
766                                60                                 0   
767                                70                                31   

     2-Hour serum insulin (mu U/ml)  \
0                                 0   
1                                 0   
2                                 0   
3                                94   
4                               168   
..                              ...   
763                             180   
764                               0   
765                             112   
766                               0   
767                               0   

     Body mass index (weight in kg/(height in m)^2)  \
0                                              33.6   
1                                              26.6   
2                                              23.3   
3                                              28.1   
4                                              43.1   
..                                              ...   
763                                            32.9   
764                                            36.8   
765                                            26.2   
766                                            30.1   
767                                            30.4   

     Diabetes pedigree function  Age (years)  Class variable  
0                         0.627           50               1  
1                         0.351           31               0  
2                         0.672           32               1  
3                         0.167           21               0  
4                         2.288           33               1  
..                          ...          ...             ...  
763                       0.171           63               0  
764                       0.340           27               0  
765                       0.245      

In [2]:
# Renaming the column Class variable

df = df.rename(columns={'Class variable': 'Class_variable'})
df

Number of times pregnant  \
0                           6   
1                           1   
2                           8   
3                           1   
4                           0   
..                        ...   
763                        10   
764                         2   
765                         5   
766                         1   
767                         1   

     Plasma glucose concentration a 2 hours in an oral glucose tolerance test  \
0                                                  148                          
1                                                   85                          
2                                                  183                          
3                                                   89                          
4                                                  137                          
..                                                 ...                          
763                                                101                          
764                                                122                          
765                                                121                          
766                                                126                          
767                                                 93                          

     Diastolic blood pressure (mm Hg)  Triceps skin fold thickness (mm)  \
0                                  72                                35   
1                                  66                                29   
2                                  64                                 0   
3                                  66                                23   
4                                  40                                35   
..                                ...                               ...   
763                                76                                48   
764                                70                                27   
765                                72                                23   
766                                60                                 0   
767                                70                                31   

     2-Hour serum insulin (mu U/ml)  \
0                                 0   
1                                 0   
2                                 0   
3                                94   
4                               168   
..                              ...   
763                             180   
764                               0   
765                             112   
766                               0   
767                               0   

     Body mass index (weight in kg/(height in m)^2)  \
0                                              33.6   
1                                              26.6   
2                                              23.3   
3                                              28.1   
4                                              43.1   
..                                              ...   
763                                            32.9   
764                                            36.8   
765                                            26.2   
766                                            30.1   
767                                            30.4   

     Diabetes pedigree function  Age (years)  Class_variable  
0                         0.627           50               1  
1                         0.351           31               0  
2                         0.672           32               1  
3                         0.167           21               0  
4                         2.288           33               1  
..                          ...          ...             ...  
763                       0.171           63               0  
764                       0.340           27               0  
765                       0.245      

In [3]:
# simple check for nulls
df.isna().sum()[df.isna().sum() > 0]

Series([], dtype: int64)

In [9]:
# eda (automated)
# profile.to_widgets() -- research to fix...

profile = ProfileReport(df)
profile.to_notebook_iframe()
profile.to_file('./reg_diabetes.html')


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
# take care of any missing values 
# n/a in this case

In [10]:
# set aside and save unseen data set
data_unseen = df.sample(n=100, random_state=42)
data        = df.drop(data_unseen.index)
print(f'Data for model: {data.shape},\nData for unseen predictions: {data_unseen.shape}')
data_unseen.to_csv('./diabetes_unseen.csv', index=False)

Data for model: (668, 9),
Data for unseen predictions: (100, 9)


In [11]:
# data.columns!='Class_variable'
X = data.loc[: , data.columns!='Class_variable']
y = data.loc[: , data.columns=='Class_variable']

In [12]:
X

Number of times pregnant  \
0                           6   
1                           1   
2                           8   
3                           1   
4                           0   
..                        ...   
762                         9   
763                        10   
765                         5   
766                         1   
767                         1   

     Plasma glucose concentration a 2 hours in an oral glucose tolerance test  \
0                                                  148                          
1                                                   85                          
2                                                  183                          
3                                                   89                          
4                                                  137                          
..                                                 ...                          
762                                                 89                          
763                                                101                          
765                                                121                          
766                                                126                          
767                                                 93                          

     Diastolic blood pressure (mm Hg)  Triceps skin fold thickness (mm)  \
0                                  72                                35   
1                                  66                                29   
2                                  64                                 0   
3                                  66                                23   
4                                  40                                35   
..                                ...                               ...   
762                                62                                 0   
763                                76                                48   
765                                72                                23   
766                                60                                 0   
767                                70                                31   

     2-Hour serum insulin (mu U/ml)  \
0                                 0   
1                                 0   
2                                 0   
3                                94   
4                               168   
..                              ...   
762                               0   
763                             180   
765                             112   
766                               0   
767                               0   

     Body mass index (weight in kg/(height in m)^2)  \
0                                              33.6   
1                                              26.6   
2                                              23.3   
3                                              28.1   
4                                              43.1   
..                                              ...   
762                                            22.5   
763                                            32.9   
765                                            26.2   
766                                            30.1   
767                                            30.4   

     Diabetes pedigree function  Age (years)  
0                         0.627           50  
1                         0.351           31  
2                         0.672           32  
3                         0.167           21  
4                         2.288           33  
..                          ...          ...  
762                       0.142           33  
763                       0.171           63  
765                       0.245           30  
766                       0.349           47  
767                       0.315           23  

[668 rows x 8 columns]

In [15]:
# split the data into training and test set
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [16]:
# encoding 
# get the categorical and numeric column names
num_cols = X_train.select_dtypes(exclude=['object']).columns.tolist()
cat_cols = X_train.select_dtypes(include=['object']).columns.tolist()
print(num_cols, '\n', cat_cols)

['Number of times pregnant', 'Plasma glucose concentration a 2 hours in an oral glucose tolerance test', 'Diastolic blood pressure (mm Hg)', 'Triceps skin fold thickness (mm)', '2-Hour serum insulin (mu U/ml)', 'Body mass index (weight in kg/(height in m)^2)', 'Diabetes pedigree function', 'Age (years)'] 
 []


In [17]:
# pipeline for numerical columns
num_pipe = make_pipeline(
    SimpleImputer(strategy='median'),
    StandardScaler()
)
num_pipe

Pipeline(steps=[('simpleimputer', SimpleImputer(strategy='median')),
                ('standardscaler', StandardScaler())])

In [18]:
# pipeline for categorical columns
cat_pipe = make_pipeline(
    SimpleImputer(strategy='constant', fill_value='N/A'),
    OneHotEncoder(handle_unknown='ignore', sparse=False)
)
cat_pipe

Pipeline(steps=[('simpleimputer',
                 SimpleImputer(fill_value='N/A', strategy='constant')),
                ('onehotencoder',
                 OneHotEncoder(handle_unknown='ignore', sparse=False))])

In [19]:
# combine both the pipelines
full_pipe = ColumnTransformer([
    ('num', num_pipe, num_cols),
    ('cat', cat_pipe, cat_cols)
])
full_pipe

ColumnTransformer(transformers=[('num',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(strategy='median')),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 ['Number of times pregnant',
                                  'Plasma glucose concentration a 2 hours in '
                                  'an oral glucose tolerance test',
                                  'Diastolic blood pressure (mm Hg)',
                                  'Triceps skin fold thickness (mm)',
                                  '2-Hour serum insulin (mu U/ml)',
                                  'Body mass index (weight in kg/(height in '
                                  'm)^2)',
                                  'Diabetes pedigree function',
                                  'Age (years)']),
                                ('cat',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(fill_value='N/A',
                                                                strategy='constant')),
                                                 ('onehotencoder',
                                                  OneHotEncoder(handle_unknown='ignore',
                                                                sparse=False))]),
                                 [])])

In [20]:
# build the model
gbr_diabetes = make_pipeline(full_pipe, GradientBoostingRegressor(random_state=42))
gbr_diabetes

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(strategy='median')),
                                                                  ('standardscaler',
                                                                   StandardScaler())]),
                                                  ['Number of times pregnant',
                                                   'Plasma glucose '
                                                   'concentration a 2 hours in '
                                                   'an oral glucose tolerance '
                                                   'test',
                                                   'Diastolic blood pressure '
                                                   '(mm Hg)',
                                                   'Triceps skin fold '
                                                   'thickness (mm)',
                                                   '2-Hour s...nsulin (mu '
                                                   'U/ml)',
                                                   'Body mass index (weight in '
                                                   'kg/(height in m)^2)',
                                                   'Diabetes pedigree function',
                                                   'Age (years)']),
                                                 ('cat',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(fill_value='N/A',
                                                                                 strategy='constant')),
                                                                  ('onehotencoder',
                                                                   OneHotEncoder(handle_unknown='ignore',
                                                                                 sparse=False))]),
                                                  [])])),
                ('gradientboostingregressor',
                 GradientBoostingRegressor(random_state=42))])

In [22]:
# train the model
gbr_diabetes.fit(X_train, y_train)


C:\Users\owner\miniconda3\envs\pc3\lib\site-packages\sklearn\ensemble\_gb.py:437: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(strategy='median')),
                                                                  ('standardscaler',
                                                                   StandardScaler())]),
                                                  ['Number of times pregnant',
                                                   'Plasma glucose '
                                                   'concentration a 2 hours in '
                                                   'an oral glucose tolerance '
                                                   'test',
                                                   'Diastolic blood pressure '
                                                   '(mm Hg)',
                                                   'Triceps skin fold '
                                                   'thickness (mm)',
                                                   '2-Hour s...nsulin (mu '
                                                   'U/ml)',
                                                   'Body mass index (weight in '
                                                   'kg/(height in m)^2)',
                                                   'Diabetes pedigree function',
                                                   'Age (years)']),
                                                 ('cat',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(fill_value='N/A',
                                                                                 strategy='constant')),
                                                                  ('onehotencoder',
                                                                   OneHotEncoder(handle_unknown='ignore',
                                                                                 sparse=False))]),
                                                  [])])),
                ('gradientboostingregressor',
                 GradientBoostingRegressor(random_state=42))])

In [24]:
# make predictions on the test set
y_pred = gbr_diabetes.predict(X_test)

In [25]:
# measure accuracy
print('R2:', r2_score(y_test, y_pred))

R2: 0.22415907844020777


In [26]:
# done manually to break out the example above
y_test['y_pred'] = y_pred
test_scores = y_test.copy()
test_scores

Class_variable    y_pred
418               0  0.068579
180               0 -0.010718
556               0  0.107478
601               0 -0.013441
317               1  0.827088
..              ...       ...
622               0  0.469301
608               0  0.374756
638               1  0.308118
247               0  0.356902
19                1  0.490692

[134 rows x 2 columns]

In [27]:
r2 = r2_score(test_scores['Class_variable'], test_scores['y_pred'])
mae = mean_absolute_error(test_scores['Class_variable'], test_scores['y_pred'])
mean_act = test_scores['Class_variable'].mean()
mean_pred = test_scores['y_pred'].mean()
mape = mean_absolute_percentage_error(test_scores['Class_variable'], test_scores['y_pred'])
print(f'R2: {r2}\nmae: {mae}\nact_mean: {mean_act}\npred_mean: {mean_pred}\nmape: {mape}')

R2: 0.22415907844020777
mae: 0.33678577565359047
act_mean: 0.39552238805970147
pred_mean: 0.3679732831419842
mape: 691517409333630.6


In [28]:
import joblib
joblib.dump(gbr_diabetes, './diabetes.pkl')
print(gbr_diabetes)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('simpleimputer',
                                                                   SimpleImputer(strategy='median')),
                                                                  ('standardscaler',
                                                                   StandardScaler())]),
                                                  ['Number of times pregnant',
                                                   'Plasma glucose '
                                                   'concentration a 2 hours in '
                                                   'an oral glucose tolerance '
                                                   'test',
                                                   'Diastolic blood pressure '
                                                   '(mm Hg)',
                                     